# Creating a crystallography table

Need to pip install `pymatgen`, `polars[all]` and `itables` 

In [15]:
from glob import glob 
from itables import init_notebook_mode

#init_notebook_mode(all_interactive=True)
#opt.maxBytes = '1MB' 

import polars as pl
import pandas as pd
import os
import re
import itables.options as opt
from pymatgen.core import Structure
from pymatgen.analysis.diffraction.xrd import XRDCalculator

In [39]:
def parse_cif(cif_file, keys=['_chemical_formula_sum', '_chemical_name_common']): 
    '''Parse `cif_file` for specific `keys`.'''
    
    with open(cif_file, 'r') as fh: 
        lines = fh.readlines()

        values_dict = {}

        for k in keys: 
            value = '??'
            for ln in lines:
                if ln.startswith(k): 
                    
                    try: 
                        value = re.split('\\s+', ln, maxsplit=1)[1]
                        value = re.sub('\n', '', value)
                    except: 
                        value = ln 
                        print(f'Could not parse key: {k} in line: {ln} in cif_file: {cif_file}') 

            values_dict[k] = value 
            
    return values_dict 

## Exploring our downloaded cif files

Oeps, *528.434 items, totalling 109,0 GB*.

In [4]:
%%time cif_files = glob('/media/frank/londev/dev/crystallography/cif/**/*.cif', recursive=True)

In [34]:
n_cifs = len(cif_files)

In [7]:
cif_basenames = [os.path.basename(f) for f in cif_files]

In [9]:
cif_i = cif_basenames.index('1011054.cif')
CdS = cif_files[cif_i]

In [ ]:
dict_list = []
for i, cf in enumerate(cif_files): 
    print(f'{i}/{n_cifs -1}', end='\r')
    d = parse_cif(cf)
    dict_list.append(d)

In [15]:
cif_df = pl.DataFrame({'cif_files': cif_files})


s = pl.Series('basenames', cif_basenames)

cif_df.insert_column(0, s);

In [16]:
cif_df

shape: (521_190, 2)
┌─────────────┬─────────────────────────────────┐
│ basenames   ┆ cif_files                       │
│ ---         ┆ ---                             │
│ str         ┆ str                             │
╞═════════════╪═════════════════════════════════╡
│ 1000000.cif ┆ /media/frank/londev/dev/crysta… │
│ 1000001.cif ┆ /media/frank/londev/dev/crysta… │
│ 1000002.cif ┆ /media/frank/londev/dev/crysta… │
│ 1000003.cif ┆ /media/frank/londev/dev/crysta… │
│ 1000004.cif ┆ /media/frank/londev/dev/crysta… │
│ …           ┆ …                               │
│ 9017922.cif ┆ /media/frank/londev/dev/crysta… │
│ 9017923.cif ┆ /media/frank/londev/dev/crysta… │
│ 9017924.cif ┆ /media/frank/londev/dev/crysta… │
│ 9017925.cif ┆ /media/frank/londev/dev/crysta… │
│ 9017926.cif ┆ /media/frank/londev/dev/crysta… │
└─────────────┴─────────────────────────────────┘

We need to extract the chemical formula from each cif_file...

In [2]:
cif_files

NameError: name 'cif_files' is not defined

In [ ]:
cif_formulas = []
n_cif = len(cif_files)

for i, f in enumerate(cif_files):
    print(f'{i}/{n_cif -1}', end='\r')
    try: 
        structure = Structure.from_file(f) 
        formula = structure.formula
    except: 
        formula = '??'
    cif_formulas.append(formula)

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'Cu': 3.0, 'Fe': 4.0, 'O': 24.0, 'P': 6.0}
  PMG={'Fe': 4.0, 'Cu': 2.9375999999999998, 'P': 6.0, 'O': 24.0}
  ratios={'O': 1.0, 'P': 1.0, 'Cu': 0.9792, 'Fe': 1.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: 2 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=primitive)[0]
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'Al': 2.7, 'N': 15.1, 'O': 0.9, 'Si': 9.3, 'Y': 0.5}
  PMG={'Y': 0.544, 'Si': 9.239999999999998, 'Al': 2.7600000000000002, 'N': 15.039999

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Missing elements Ti from CIF-reported composition
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Missing elements H from PMG structure composition
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: Structure has implicit hydrogens defined, parsed structure unlikely to be suitable for use in calculations unless hydrogens added.
5 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=primitive)[0]
/home/frank/.config/jupyterlab-desktop/jlab_

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: 4 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=primitive)[0]
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1027: UserWarning: No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
  self.symmetry_operations = self.get_symops(data)
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
  struct = parser.parse_structures(primitive=primitive)[0]


/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Some occupancies ([5.0]) sum to > 1! If they are within the occupancy_tolerance, they will be rescaled. The current occupancy_tolerance is set to: 1.0
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: No structure parsed for section 1 in CIF.
Occupancy 5.0 exceeded tolerance.
  struct = parser.parse_structures(primitive=primitive)[0]
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: Structure has implicit hydrogens defined, parsed structure unlikely to be suitable for use in calculations unless hydrogens added.
Some occupancies ([5.0]) sum to > 1! If they are within the occupancy_tolerance, they 

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: Structure has implicit hydrogens defined, parsed structure unlikely to be suitable for use in calculations unless hydrogens added.
2 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=primitive)[0]
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Some occupancies ([1.25]) sum to > 1! If they are within the occupancy_tolerance, they will be rescaled. The current occupancy_tolerance is set to: 1.0
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: No structure parsed for section 1 in CIF.
Occupancy 1.25 exceeded toleran

...

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'C': 20.0, 'H': 21.0, 'Cl': 4.0, 'Cu': 2.0, 'N': 10.0, 'O': 1.5, 'S': 2.0}
  PMG={'Cu': 4.0, 'H': 36.0, 'C': 40.0, 'S': 4.0, 'N': 20.0, 'Cl': 8.0, 'O': 3.0}
  ratios={'Cl': 2.0, 'H': 1.7142857142857142, 'Cu': 2.0, 'N': 2.0, 'O': 2.0, 'S': 2.0, 'C': 2.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'C': 24.0, 'H': 39.5, 'Cl': 1.0, 'N': 8.0, 'O': 8.25, 'Pt': 1.0, 'S': 1.0}
  PMG={'H': 148.0, 'Pt': 4.0, 'C': 96.0, 'S': 4.0, 'N': 32.0, 'Cl': 4.0, 'O': 33.0}
  ratios={'Cl': 4.0, 'H': 3.7468354430379747, 'N': 4.0, 'O': 4.0, 'S': 4.0, 'Pt': 4.0, 'C': 4.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'C': 28.0, 'H': 37.0, 'Cl': 1.0, 'N': 8.0, 'O': 10.0, 'Pt': 1.0, 'S': 1.0}
  PMG={'H': 188.0, 'Pt': 6.0, 'C': 168.0, 'S': 6.0, 'N': 48.0, 'Cl': 6.0, 'O': 60.0}
  ratios={'Cl': 6.0, 'H': 5.081081081081081, 'N': 6.0, 'O': 6.0, 'S': 6.0, 'Pt': 6.0, 'C': 6.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):


/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'C': 23.0, 'H': 36.0, 'Cl': 1.0, 'Cu': 1.0, 'N': 5.0, 'O': 8.0}
  PMG={'Cu': 8.0, 'H': 272.0, 'C': 184.0, 'N': 40.0, 'Cl': 8.0, 'O': 64.0}
  ratios={'Cl': 8.0, 'H': 7.555555555555555, 'Cu': 8.0, 'N': 8.0, 'O': 8.0, 'C': 8.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):


/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'C': 35.9, 'H': 42.95, 'Cl': 2.0, 'N': 5.0, 'O': 4.08, 'Os': 1.0}
  PMG={'H': 83.50000000000003, 'Os': 2.0, 'C': 71.80000000000001, 'N': 10.0, 'Cl': 4.0, 'O': 8.4}
  ratios={'Cl': 2.0, 'H': 1.944121071012806, 'N': 2.0, 'O': 2.058823529411765, 'C': 2.0000000000000004, 'Os': 2.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'C': 32.0, 'H': 32.5, 'Cl': 2.0, 'N': 4.0, 'O': 0.25, 'Os': 1.0}
  PMG={'H': 128.0, 'Os': 4.0, 'C': 128.0, 'N': 16.0, 'Cl': 8.0, 'O': 1.0}
  ratios={'Cl': 4.0, 'H': 3.9384615384615387, 'N': 4.0, 'O': 4.0, 'C': 4.0, 'Os': 4.0}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.conf

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'Ca': 1.9, 'Mg': 0.17, 'O': 44.11, 'Si': 16.0}
  PMG={'Ca': 7.680000000000001, 'Mg': 0.6719999999999999, 'Si': 64.0, 'O': 178.28799999999995}
  ratios={'O': 4.041895261845386, 'Si': 4.0, 'Ca': 4.042105263157895, 'Mg': 3.9529411764705875}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/io/cif.py:1312: UserWarning: Incorrect stoichiometry:
  CIF={'Ca': 1.9, 'Mg': 0.17, 'O': 36.44, 'Si': 16.0}
  PMG={'Ca': 7.6, 'Mg': 0.7199999999999999, 'Si': 64.0, 'O': 145.79999999999973}
  ratios={'O': 4.001097694840827, 'Si': 4.0, 'Ca': 4.0, 'Mg': 4.235294117647058}
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-pack

In [20]:
cif_formulas

['Al4 P8 H68 C20 N8 O32',
 'H568 C428 N56 O104',
 '??',
 '??',
 'Cu2 P4 H60 C58 I2',
 'Sr20 V12 H12 O24 F64',
 'H100 C88 N8 Cl4 O32',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Al12 O18',
 'H88 C52 O12',
 'H68 C68 N4 O8']

In [45]:
CdS_file = cif_files[cif_basenames.index('1011054.cif')]

Now we need to inspect the structure information...

In [49]:
CdS_structure = Structure.from_file(CdS_file)

/home/frank/.config/jupyterlab-desktop/jlab_server/lib/python3.12/site-packages/pymatgen/core/structure.py:3087: UserWarning: Issues encountered while parsing CIF: 4 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=primitive)[0]


In [47]:
CdS_structure.as_dict()

{'@module': 'pymatgen.core.structure',
 '@class': 'Structure',
 'charge': 0.0,
 'lattice': {'matrix': [[4.15, 0.0, 2.541142108230758e-16],
   [-2.074999999999999, 3.5940054257054213, 2.541142108230758e-16],
   [0.0, 0.0, 6.737]],
  'pbc': (True, True, True),
  'a': 4.15,
  'b': 4.15,
  'c': 6.737,
  'alpha': 90.0,
  'beta': 90.0,
  'gamma': 119.99999999999999,
  'volume': 100.48318039485632},
 'properties': {},
 'sites': [{'species': [{'element': 'Cd',
     'oxidation_state': 2.0,
     'spin': None,
     'occu': 1.0}],
   'abc': [0.3333333333333333, 0.6666666666666666, 0.0],
   'properties': {},
   'label': 'Cd1',
   'xyz': [8.881784197001252e-16, 2.396003617136947, 2.541142108230758e-16]},
  {'species': [{'element': 'Cd',
     'oxidation_state': 2.0,
     'spin': None,
     'occu': 1.0}],
   'abc': [0.6666666666666667, 0.33333333333333337, 0.5],
   'properties': {},
   'label': 'Cd1',
   'xyz': [2.0750000000000006, 1.1980018085684738, 3.3685000000000005]},
  {'species': [{'element': '

In [48]:
CdS_structure.formula

'Cd2 S2'

In [50]:
cif_df

shape: (521_190, 1)
┌─────────────────────────────────┐
│ cif_files                       │
│ ---                             │
│ str                             │
╞═════════════════════════════════╡
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ …                               │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
│ /media/frank/londev/dev/crysta… │
└─────────────────────────────────┘

In [59]:
cif_df['cif_basenames'] = cif_basenames

In [60]:
cif_df

cif_files cif_basenames
0       /media/frank/londev/dev/crystallography/cif/1/...   1000000.cif
1       /media/frank/londev/dev/crystallography/cif/1/...   1000001.cif
2       /media/frank/londev/dev/crystallography/cif/1/...   1000002.cif
3       /media/frank/londev/dev/crystallography/cif/1/...   1000003.cif
4       /media/frank/londev/dev/crystallography/cif/1/...   1000004.cif
...                                                   ...           ...
521185  /media/frank/londev/dev/crystallography/cif/9/...   9017922.cif
521186  /media/frank/londev/dev/crystallography/cif/9/...   9017923.cif
521187  /media/frank/londev/dev/crystallography/cif/9/...   9017924.cif
521188  /media/frank/londev/dev/crystallography/cif/9/...   9017925.cif
521189  /media/frank/londev/dev/crystallography/cif/9/...   9017926.cif

[521190 rows x 2 columns]

In [63]:
cif_files[10:20]

['/media/frank/londev/dev/crystallography/cif/1/00/00/1000010.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000011.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000012.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000013.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000014.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000015.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000016.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000017.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000018.cif',
 '/media/frank/londev/dev/crystallography/cif/1/00/00/1000019.cif']

In [ ]:
cif_formulas = []
n_cif = len(cif_files)

for i, f in enumerate(cif_files[0:20]):
    print(f'{i}/{n_cif -1}', end='\r')
    try: 
        formula = Structure.from_file(f) 
    except: 
        formula = '??'
    cif_formulas.append(formula)

In [65]:
cif_formulas

['Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Ca4 Mg4 Si8 O24',
 'Al12 O18',
 'H88 C52 O12',
 'H68 C68 N4 O8']